# Population of the Knowledge DB - V4 #

### Load libraries and connect to Virtuoso

In [3]:
import os 
import re
import logging
import sys
import pyodbc
import hashlib
import pandas as pd
from datetime import datetime
from SPARQLWrapper import SPARQLWrapper, POST, DIGEST, GET
from SPARQLWrapper import JSON, INSERT, DELETE
import sparql_dataframe
from itertools import chain

In [4]:
def connect_db(DSN, DBA, UID, PWD):

    connection = pyodbc.connect('DSN={};DBA={};UID={};PWD={}'.format(DSN, 
                                                                     DBA,
                                                                     UID,
                                                                     PWD))
    cursor = connection.cursor()

    return connection, cursor


def connect_virtuoso(DSN, UID, PWD):

    sparql = SPARQLWrapper(DSN)
    sparql.setHTTPAuth(DIGEST)
    sparql.setCredentials(UID, PWD)
    sparql.setMethod(GET)

    return sparql


Replace the values with your own logins :

In [5]:
user = "dba"
login = "30gFcpQzj7sPtRu5bkes"

In [6]:
# Connection to CDB 
connection, cursor = connect_db('Virtuoso All', 
                                'ESTAT', 
                                user, 
                                login)


# Connection to the KDB 
endpoint = "http://virtuoso-test.kapcode.fr:8890/sparql/"
sparql = connect_virtuoso(endpoint, 
                          user, 
                          login)


### Define content selection functions

In [7]:
def select_query(columns, table, conditions=None): 

    if conditions:

        query = """
            SELECT {}
            FROM {}
            WHERE {}

        """.format(columns, table, conditions)

    else:

        query = """

        SELECT {}
        FROM {}
        """.format(columns, table)

    return query

#### Get all tables name from the CDB 

In [8]:
ESTAT_V1_tables_names = pd.read_sql(select_query('*',
                                          'ESTAT.information_schema.tables', 
                                          ''), 
                             connection)
ESTAT_V1_tables_names['TABLE_NAME']

0                     dat_article
1           dat_article_paragraph
2         dat_article_shared_link
3                dat_code_dataset
4                   dat_code_dico
5                     dat_dataset
6              dat_estat_glossary
7     dat_estatg_measurement_unit
8            dat_estatg_stat_unit
9                dat_further_info
10                   dat_glossary
11                  dat_link_info
12           dat_paragraph_figure
13               dat_redirections
14           dat_related_concepts
15                    dat_sources
16           dat_statistical_data
17           mod_article_division
18               mod_concept_type
19                mod_dictionnary
20           mod_measurement_unit
21             mod_ramon_category
22       mod_resource_information
23              mod_resource_type
24           mod_statistical_unit
25          tm_articles_to_topics
26                       tm_terms
27                      tm_topics
28                      tm_values
Name: TABLE_NA

##### Load the Link info table 

In [9]:
ESTAT_V1_dat_link_info = pd.read_sql(select_query('*',
                                          ' ESTAT.V1.dat_link_info', 
                                          ''), 
                             connection)
print(ESTAT_V1_dat_link_info.shape)



(10557, 5)


In [10]:
ESTAT_V1_dat_link_info.head()

id                                              title  \
0   1                             Accident at work         
1   2          Accidents at work (ESAW, 2008 onwards)      
2   3          Commission Regulation (EU) No 349/2011      
3   4     European Statistics on Accidents at Work (E...   
4   5                          Fatal accident at work      

                                                 url  resource_information_id  \
0  https://ec.europa.eu/eurostat/statistics-expla...                        1   
1  http://ec.europa.eu/eurostat/cache/metadata/en...                        1   
2  http://eur-lex.europa.eu/LexUriServ/LexUriServ...                       16   
3  http://ec.europa.eu/eurostat/product?code=KS-R...                        1   
4  https://ec.europa.eu/eurostat/statistics-expla...                        1   

   resource_type_id  
0                 3  
1                11  
2                 2  
3                 0  
4                 3

##### Load the Resources info and types tables

In [11]:
ESTAT_V1_mod_resource_information = pd.read_sql(select_query('*',
                                          ' ESTAT.V1.mod_resource_information', 
                                          ''), 
                             connection)
ESTAT_V1_mod_resource_type = pd.read_sql(select_query('*',
                                          ' ESTAT.V1.mod_resource_type', 
                                          ''), 
                             connection)             

In [12]:
#def format_ressource_type(string):
#  string = string.lower()
#  string = string.replace(" ","-").strip()
#  return string
#ESTAT_V1_mod_resource_type["formatted_label"] = ESTAT_V1_mod_resource_type.label.apply(format_ressource_type)


##### Load Glossary related tables

In [14]:
ESTAT_V1_dat_glossary = pd.read_sql(select_query('*',
                                          'ESTAT.V1.dat_glossary', 
                                          ''), 
                             connection)

ESTAT_V1_dat_related_concepts = pd.read_sql(select_query('*',
                                          "ESTAT.V1.dat_related_concepts", 
                                          ''), 
                                            connection)      

ESTAT_V1_dat_sources = pd.read_sql(select_query('*',
                                          "ESTAT.V1.dat_sources", 
                                          ''), 
                             connection)
ESTAT_V1_dat_redirections = pd.read_sql(select_query('*',
                                          "ESTAT.V1.dat_redirections", 
                                          ''), 
                             connection)

ESTAT_V1_dat_further_info = pd.read_sql(select_query('*',
                                          'ESTAT.V1.dat_further_info', 
                                          ''), 
                             connection)
ESTAT_V1_dat_statistical_data = pd.read_sql(select_query('*',
                                          'ESTAT.V1.dat_statistical_data', 
                                          ''), 
                             connection)

##### Load Statistical Articles related tables

In [15]:
ESTAT_V1_dat_article_shared_link = pd.read_sql(select_query('*',
                                          'ESTAT.V1.dat_article_shared_link', 
                                          ''), 
                             connection)


In [16]:
ESTAT_V1_mod_article_division = pd.read_sql(select_query('*',
                                          'ESTAT.V1.mod_article_division', 
                                          ''), 
                             connection)

In [17]:
ESTAT_V1_dat_article_paragraph = pd.read_sql(select_query('*',
                                          'ESTAT.V1.dat_article_paragraph', 
                                          ''), 
                             connection)

In [18]:
ESTAT_V1_dat_paragraph_figure = pd.read_sql(select_query('*',
                                          'ESTAT.V1.dat_paragraph_figure', 
                                          ''), 
                             connection)

In [19]:
ESTAT_V1_dat_article = pd.read_sql(select_query('*',
                                          'ESTAT.V1.dat_article', 
                                          'background_article = 0'), 
                             connection)

ESTAT_V1_dat_article_core_data = pd.read_sql('SELECT article_id, link_id, url, data_sources FROM ESTAT.V1.dat_article_shared_link INNER JOIN ESTAT.V1.dat_article ON ESTAT.V1.dat_article.id = article_id INNER JOIN ESTAT.V1.dat_link_info ON link_id = ESTAT.V1.dat_link_info.id WHERE background_article = 0 AND article_division_id=1',connection)

##### Load Statistical Background Articles related tables

In [21]:
ESTAT_V1_dat_background_article = pd.read_sql(select_query('*',
                                          'ESTAT.V1.dat_article', 
                                          'background_article = 1'), 
                             connection)

ESTAT_V1_dat_background_article_core_data = pd.read_sql('SELECT article_id, link_id, url, data_sources FROM ESTAT.V1.dat_article_shared_link INNER JOIN ESTAT.V1.dat_article ON ESTAT.V1.dat_article.id = article_id INNER JOIN ESTAT.V1.dat_link_info ON link_id = ESTAT.V1.dat_link_info.id WHERE background_article = 1 AND article_division_id=1',connection)

### Populate the KDB

###  2 - Insertion of Glossary elements into the KDB. 

In [22]:
## Find the homepage : 
SEGlossary_homepage_id = ESTAT_V1_dat_glossary.loc[ESTAT_V1_dat_glossary['homepage']==1]['id'].item()

In [23]:
def decode_string(string):
  string = string.encode("ascii", "ignore")
  string_decode = string.decode()
  return string_decode
ESTAT_V1_dat_glossary.definition = ESTAT_V1_dat_glossary.definition.apply(decode_string)


In [24]:
def insert_glossary_elements(DB, link_info_table, mod_resource_info_table, mod_resource_type_table, redirections_table, method, homepage_id): 

    
    for i, row in DB.iterrows():
        print(i)
        id_ = row["id"]
        definition_ = row["definition"]
        definition_ = definition_.replace("'","").strip()
        definition_ = definition_.replace("\\","").strip()
        last_update_ = str(row["last_update"])
        homepage_ = row["homepage"]
        #redirection_ = row["redirection"]
         # Get info from the eurostat_links
        title_ = link_info_table[link_info_table['id'] == id_].title.item()
        title_ = title_.replace("'","").strip()
        url_ = link_info_table[link_info_table['id'] == id_].url.item()
        resourcetype_id_ = link_info_table.loc[link_info_table['id'] == id_]['resource_type_id'].item()
        resourceinfo_id_ = link_info_table.loc[link_info_table['id'] == id_]['resource_information_id'].item() 
        #get the label from resourcetype and info  id
        resourceinfo_ = mod_resource_info_table.loc[mod_resource_info_table['id'] == resourceinfo_id_]['uri'].item() 
        resourcetype_ = mod_resource_type_table.loc[mod_resource_type_table['id'] == resourcetype_id_]['uri'].item() 
        
        #get original title for redirected pages 
        if id_ in redirections_table.glossary_id.values :
            OT_query_part = []
            for link_id_ in redirections_table[redirections_table['glossary_id'] == id_].link_id :
                original_title_ = link_info_table[link_info_table['id'] == link_id_].title.item()
                subpart = "SEG:" + str(id_) + """ skos:altLabel '""" + str(original_title_) + "'."
                OT_query_part.append(subpart)
            OT_query_part = '\n'.join(OT_query_part)
            #print(redirections_table[redirections_table['glossary_id'] == id_].link_id)
            #redirection_id_ = redirections_table[redirections_table['glossary_id'] == id_].link_id.item()
            #original_title_ = link_info_table[link_info_table['id'] == redirection_id_].title.item()
            #OT_query_part = "SEG:" + str(id_) + """ skos:altLabel '""" + str(original_title_) + "'."
        else :
            OT_query_part = ""
            
        #Distinguish the homepage from the rest 
        if id_ != homepage_id :        
            concept_query_part = "SEG:" + str(id_) + """ skos:Concept SEG:""" +  str(id_) + "."
            title_query_part = "SEG:" + str(id_) + """ skos:prefLabel '""" +  str(title_) + "'."
            def_query_part = "SEG:" + str(id_) + """ skos:definition '""" +  str(definition_) + "'."
            #extraction_query_part = ""
            topconcept_query_part = ""
            publisher_query_part = ""
            inscheme_query_part = """SEG:""" + str(id_) +  """ skos:inScheme 'https://nlp4statref/knowledge/resource/vocabulary/glossary/statistics-explained-glossary'."""

            #exactmatch_query_part_1 = """SEG:""" + str(id_) +  """skos:exactMatch estat:EurostatConcept."""
            #exactmatch_query_part_2 = """SEG:""" + str(id_) +  """skos:exactMatch estat:NamedEntities."""

        else :
            concept_query_part = "SEG:" + str(id_) + """ skos:ConceptScheme  'https://nlp4statref/knowledge/resource/vocabulary/glossary/statistics-explained-glossary'."""
            title_query_part = "SEG:" + str(id_) + """ dct:title '""" +  str(title_) + "'."
            def_query_part = "SEG:" + str(id_) + """ dct:description '""" +  str(definition_) + "'."
            #extraction_query_part = scraping date ? 
            topconcept_query_part = []
            for concept_id_ in DB.id:
                if concept_id_ != homepage_id : 
                    subpart = "SEG:" + str(homepage_id) + """ skos:hasTopConcept SEG:""" +  str(concept_id_) + "."
                    topconcept_query_part.append(subpart)
            topconcept_query_part = '\n'.join(topconcept_query_part)
            publisher_query_part = """SEG:""" + str(id_) +  """ dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'."""
            inscheme_query_part = ""
            #exactmatch_query_part_1 = ""
            #exactmatch_query_part_2 = ""
                  
    
        # Construct the query 
        query = """

            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SEG: <https://nlp4statref/knowledge/resource/statistics-explained-glossary#>

            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              """ + concept_query_part + """ 
              """ + inscheme_query_part + """              
              """ + topconcept_query_part + """
              """ + title_query_part + """
              """ + def_query_part + """
              """ + publisher_query_part + """
              """ + OT_query_part + """
              SEG:""" + str(id_) + """ dct:modified '""" + str(last_update_) + """'.
              SEG:""" + str(id_) + """ dct:source '""" + str(url_) + """'.  
              SEG:""" + str(id_) + """ dct:type '""" + str(resourcetype_) + """'.
              SEG:""" + str(id_) + """ estat:resourceInformation '""" + str(resourceinfo_) + """'.  
             
              
              
        } }
        ;
            """
        #Take out special characters : 
        query.encode('latin-1')
        print(query)
        sparql.setQuery(query)
        sparql.method = method
        sparql.setReturnFormat(JSON)
        results = sparql.query().response.read()

In [25]:
###run the function 
insert_glossary_elements(DB = ESTAT_V1_dat_glossary,
                         link_info_table = ESTAT_V1_dat_link_info,
                         mod_resource_info_table = ESTAT_V1_mod_resource_information,
                         mod_resource_type_table = ESTAT_V1_mod_resource_type,
                         redirections_table = ESTAT_V1_dat_redirections,
                         method = 'POST', homepage_id = SEGlossary_homepage_id) 

0


            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SEG: <https://nlp4statref/knowledge/resource/statistics-explained-glossary#>

            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SEG:1 skos:Concept SEG:1. 
              SEG:1 skos:inScheme 'https://nlp4statref/knowledge/resource/vocabulary/glossary/statistics-explained-glossary'.              
              
              SEG:1 skos:prefLabel 'Accident at work'.
              SEG:1 skos:definition 'An     accident at work    in the framework of the administrative data collection on European Statistics on Accidents at Work (ESAW) is a discrete occurrence during the course of work which leads to physical or mental harm. The phrase in the course of work means whilst engaged in an occupational activity or during the time spent at work. This includes cases of road traffic accidents in the course of work but exclud

5


            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SEG: <https://nlp4statref/knowledge/resource/statistics-explained-glossary#>

            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SEG:10 skos:Concept SEG:10. 
              SEG:10 skos:inScheme 'https://nlp4statref/knowledge/resource/vocabulary/glossary/statistics-explained-glossary'.              
              
              SEG:10 skos:prefLabel 'Gross domestic product (GDP)'.
              SEG:10 skos:definition 'Gross domestic product    , abbreviated as     GDP    , is a basic measure of the overall size of a countrys economy.    As an     aggregate    measure of production, GDP is equal to the sum of the gross     value added    of all resident institutional units engaged in production, plus any taxes on products and minus any subsidies on products. Gross value added is the difference between output and 

9


            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SEG: <https://nlp4statref/knowledge/resource/statistics-explained-glossary#>

            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SEG:15 skos:Concept SEG:15. 
              SEG:15 skos:inScheme 'https://nlp4statref/knowledge/resource/vocabulary/glossary/statistics-explained-glossary'.              
              
              SEG:15 skos:prefLabel 'Railway'.
              SEG:15 skos:definition 'A     railway    is a line of communication between two or more geographic locations consisting, usually, of one or more     railway lines    constructed from two parallel steel rails that is for the exclusive use of railway vehicles.'.
              
              
              SEG:15 dct:modified '2013-02-28 10:16:00'.
              SEG:15 dct:source 'https://ec.europa.eu/eurostat/statistics-explained/index.php?titl

15


            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SEG: <https://nlp4statref/knowledge/resource/statistics-explained-glossary#>

            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SEG:27 skos:Concept SEG:27. 
              SEG:27 skos:inScheme 'https://nlp4statref/knowledge/resource/vocabulary/glossary/statistics-explained-glossary'.              
              
              SEG:27 skos:prefLabel 'Letter box'.
              SEG:27 skos:definition 'A     letter box    is a facility provided for the public either on the public highways or at the premises of the universal service provider, where postal items may be deposited with the public postal network by customers.    The count of letter boxes should refer to the number of geographical points, where letter boxes are located, i.e. where several letter boxes are situated together at the same place, they shoul

21


            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SEG: <https://nlp4statref/knowledge/resource/statistics-explained-glossary#>

            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SEG:33 skos:Concept SEG:33. 
              SEG:33 skos:inScheme 'https://nlp4statref/knowledge/resource/vocabulary/glossary/statistics-explained-glossary'.              
              
              SEG:33 skos:prefLabel 'Expenditure on pensions'.
              SEG:33 skos:definition 'Expenditure on pensions    comprises the following social benefits: disability pension, early retirement due to reducedcapacity to work, old-age pension, anticipated old-age pension, partial pension, survivors pension and early retirement due for labour market reasons.'.
              
              
              SEG:33 dct:modified '2021-04-19 16:45:00'.
              SEG:33 dct:source 'https://ec.eu

...

1285


            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SEG: <https://nlp4statref/knowledge/resource/statistics-explained-glossary#>

            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SEG:2256 skos:Concept SEG:2256. 
              SEG:2256 skos:inScheme 'https://nlp4statref/knowledge/resource/vocabulary/glossary/statistics-explained-glossary'.              
              
              SEG:2256 skos:prefLabel 'Bank for International Settlements (BIS)'.
              SEG:2256 skos:definition 'The     Bank for International Settlements    , abbreviated as     BIS    , is the oldest international financial institution and was established on 17 May 1930 in the context of the Young Plan (which dealt with the issue of the reparation payments imposed on Germany by the Treaty of Versailles following the First World War). The head office is in Basel, Switzerland and the

1291


            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SEG: <https://nlp4statref/knowledge/resource/statistics-explained-glossary#>

            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SEG:2268 skos:Concept SEG:2268. 
              SEG:2268 skos:inScheme 'https://nlp4statref/knowledge/resource/vocabulary/glossary/statistics-explained-glossary'.              
              
              SEG:2268 skos:prefLabel 'Backfilling'.
              SEG:2268 skos:definition 'Backfilling    means a recovery operation where suitable waste is used for reclamation purposes in excavated areas or for engineering purposes in landscaping and where the waste is a substitute for non-waste materials.'.
              
              
              SEG:2268 dct:modified '2019-07-12 14:24:00'.
              SEG:2268 dct:source 'https://ec.europa.eu/eurostat/statistics-explained/index.php

1297


            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SEG: <https://nlp4statref/knowledge/resource/statistics-explained-glossary#>

            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SEG:2284 skos:Concept SEG:2284. 
              SEG:2284 skos:inScheme 'https://nlp4statref/knowledge/resource/vocabulary/glossary/statistics-explained-glossary'.              
              
              SEG:2284 skos:prefLabel 'Arrival of tourist at a tourist accommodation establishment'.
              SEG:2284 skos:definition 'See      arrival disambiguation page     for other meanings of arrival.    Within the context of     European Union (EU)     tourism statistics    , an     arrival    is defined as a     tourist    who arrives at a     tourist accommodation establishment (rented accommodation)    or at a     non-rented accommodation    ; in the scope of the Tourism Regula

1303


            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SEG: <https://nlp4statref/knowledge/resource/statistics-explained-glossary#>

            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SEG:2298 skos:Concept SEG:2298. 
              SEG:2298 skos:inScheme 'https://nlp4statref/knowledge/resource/vocabulary/glossary/statistics-explained-glossary'.              
              
              SEG:2298 skos:prefLabel 'Areas facing natural constraints'.
              SEG:2298 skos:definition 'Areas facing natural constraints    are areas in which European Union Member States or regions may grant payments to farmers to compensate for production difficulties occasioned by particular biophysical aspects of the environment, as defined in rural development rules relating to the common agricultural policy.'.
              
              
              SEG:2298 dct:modified '2

1309


            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SEG: <https://nlp4statref/knowledge/resource/statistics-explained-glossary#>

            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SEG:2319 skos:Concept SEG:2319. 
              SEG:2319 skos:inScheme 'https://nlp4statref/knowledge/resource/vocabulary/glossary/statistics-explained-glossary'.              
              
              SEG:2319 skos:prefLabel 'Actual individual consumption (AIC)'.
              SEG:2319 skos:definition 'Actual individual consumption    , abbreviated as     AIC    , refers to all goods and services actually consumed by     households    . It encompasses consumer goods and services purchased directly by households, as well as services provided by     non-profit institutions    and the     government    for individual consumption (e.g., health and education services). In internati

In [26]:
def insert_glossary_elements_relations(DB, link_info_table, sources_table, SEG_table, BGA_table, SA_table, SED_table, method):      
    
    for i, row in DB.iterrows():
        concept_id_ = row["glossary_id"]
        link_id_ = row["link_id"] #concept et link sont de la meme sequence unique. 
        #Get the resource type from the eurostat_links
        resourcetype_id_ = link_info_table.loc[link_info_table['id'] == link_id_]['resource_type_id'].item()
        relation_ = ""
        if (resourcetype_id_ in [2]): relation_ = "estat:relatedLegallnformation"
        if (resourcetype_id_ in [1,6,7,8,9,10]): relation_ = "estat:relatedEditorialContent"
        if (resourcetype_id_ in [11,12,13,14]): relation_ = "estat:relatedStatisticData"
        if (relation_ != "") :
            #Get the prefix   
            o_prefix = ""
            if (link_id_ in SEG_table.id.values): o_prefix = " SEG:"
            if (link_id_ in BGA_table.id.values): o_prefix = " BGA:"
            if (link_id_ in SA_table.id.values): o_prefix = " SA:"
            if (link_id_ in SED_table.article_id.values): o_prefix = " SED:"
            if (o_prefix != "") :
                
                # Add source info if it exists : 
                source_link = ""
                if (concept_id_ in sources_table.glossary_id.values):
                    if (link_id_ in sources_table.loc[sources_table['glossary_id'] == concept_id_]['link_id'].values):
                        source_link = sources_table.loc[sources_table['glossary_id'] == concept_id_]['link_id'].item()
                        if (source_link != ""): source_query_part = """SEG:""" + str(id_) + """ estat:sourceInformation '""" + o_prefix  + str(link_id_) + """."""
                        else : source_query_part = ""
                # Construct the query 
                query = """
                    PREFIX SEG: <https://nlp4statref/knowledge/resource/statistics-explained-glossary#>
                    PREFIX BGA: <https://nlp4statref/knowledge/resource/background-article#>
                    PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
                    PREFIX SED: <https://nlp4statref/knowledge/resource/statistics-explained-data#>

                    PREFIX estat: <https://nlp4statref/knowledge/ontology/> 
                    PREFIX skos: <http://www.w3.org/2004/02/skos/core#>

                    INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                       SEG:""" + str(concept_id_) + ' ' + relation_ + o_prefix  + str(link_id_) + """. 
                       """ + source_query_part + """
                    } }
                    ;
                """
                print(query)
                sparql.setQuery(query)
                sparql.method = method
                sparql.setReturnFormat(JSON)
                results = sparql.query().response.read()

In [27]:
insert_glossary_elements_relations(DB = ESTAT_V1_dat_further_info,
                                   link_info_table = ESTAT_V1_dat_link_info,
                                   sources_table= ESTAT_V1_dat_sources,
                                   SEG_table = ESTAT_V1_dat_glossary,  
                                   BGA_table=ESTAT_V1_dat_background_article,
                                   SA_table=ESTAT_V1_dat_article, 
                                   SED_table=ESTAT_V1_dat_article_core_data,
                                   method = 'POST')

In [28]:
insert_glossary_elements_relations(ESTAT_V1_dat_statistical_data,
                                   link_info_table = ESTAT_V1_dat_link_info,
                                   sources_table= ESTAT_V1_dat_sources,
                                   SEG_table = ESTAT_V1_dat_glossary,  
                                   BGA_table=ESTAT_V1_dat_background_article,
                                   SA_table=ESTAT_V1_dat_article, 
                                   SED_table=ESTAT_V1_dat_article_core_data,
                                   method = 'POST')

###  3 - Insertion of Statistical Explained elements into the KDB. 

###  3.1 - Insertion of Statistical Explained articles

In [29]:
## Find the homepage : 
SA_homepage_id = ESTAT_V1_dat_article.loc[ESTAT_V1_dat_article['homepage']==1]['id'].item()

In [32]:
def insert_dat_article(DB, article_shared_link_table, link_info_table, mod_resource_info_table, mod_resource_type_table, homepage_id, method): 

    for i, row in DB.iterrows():

        id_ = row['id']
        if id_ != homepage_id :    
            last_update_ = str(row["last_update"])

            # Get info from the eurostat_links
            title_ = link_info_table[link_info_table['id'] == id_].title.item()
            title_ = title_.replace("'","").strip()
            url_ = link_info_table[link_info_table['id'] == id_].url.item()
            resourcetype_id_ = link_info_table.loc[link_info_table['id'] == id_]['resource_type_id'].item()
            resourceinfo_id_ = link_info_table.loc[link_info_table['id'] == id_]['resource_information_id'].item() 
            #get the label from resourcetype and info  id
            resourceinfo_ = mod_resource_info_table.loc[mod_resource_info_table['id'] == resourceinfo_id_]['uri'].item() 
            resourcetype_ = mod_resource_type_table.loc[mod_resource_type_table['id'] == resourcetype_id_]['uri'].item() 
            # add source data 
            shared_links = article_shared_link_table[article_shared_link_table['article_id'] == id_]
            if (1 in shared_links['article_division_id'].values) : 
                shared_links_source = shared_links.loc[shared_links['article_division_id']==1]['link_id'].values
                source_query_part = []
                for val in shared_links_source: # if multiple values 
                    subpart = """SA:""" + str(id_) + """ estat:sourceData SDR:"""   + str(val) + """."""
                    source_query_part.append(subpart)
                source_query_part = '\n'.join(source_query_part)      
            else : source_query_part = ""
            # Construct the query 
            query = """

                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SA:""" + str(id_) + """ estat:StatisticalArticle SA:""" + str(id_) + """.
                  SA:""" + str(id_) + """ dct:type '""" + str(resourcetype_) + """'.
                  SA:""" + str(id_) + """ dct:title '""" + str(title_) + """'.  
                  SA:""" + str(id_) + """ dct:description 'Statistics Explained article'.
                  SA:""" + str(id_) + """ dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SA:""" + str(id_) + """ estat:resourceInformation '""" + str(resourceinfo_) + """'.
                  SA:""" + str(id_) + """ dct:modified '""" + str(last_update_) + """'.
                  SA:""" + str(id_) + """ dct:source '""" + str(url_) + """'.  
                  """ + source_query_part + """

            } }
            ;
                """
            print(query)
            sparql.setQuery(query)
            sparql.method = method
            sparql.setReturnFormat(JSON)
            results = sparql.query().response.read()

In [33]:
insert_dat_article(DB = ESTAT_V1_dat_article,
                   article_shared_link_table = ESTAT_V1_dat_article_shared_link,
                              link_info_table = ESTAT_V1_dat_link_info,
                              mod_resource_info_table = ESTAT_V1_mod_resource_information,
                              mod_resource_type_table = ESTAT_V1_mod_resource_type,
                              homepage_id =  SA_homepage_id,
                              method = "POST")



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SA:7 estat:StatisticalArticle SA:7.
                  SA:7 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistical-article'.
                  SA:7 dct:title 'Accidents at work statistics'.  
                  SA:7 dct:description 'Statistics Explained article'.
                  SA:7 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SA:7 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SA:7 dct:modified '2020-11-26 16:06:00'.




                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SA:51 estat:StatisticalArticle SA:51.
                  SA:51 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistical-article'.
                  SA:51 dct:title 'Road freight transport by vehicle characteristics'.  
                  SA:51 dct:description 'Statistics Explained article'.
                  SA:51 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SA:51 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SA:51 dct:mod



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SA:116 estat:StatisticalArticle SA:116.
                  SA:116 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistical-article'.
                  SA:116 dct:title 'Agricultural production - livestock and meat'.  
                  SA:116 dct:description 'Statistics Explained article'.
                  SA:116 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SA:116 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SA:116 dct:



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SA:178 estat:StatisticalArticle SA:178.
                  SA:178 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistical-article'.
                  SA:178 dct:title 'SDG 17 - Partnerships for the goals'.  
                  SA:178 dct:description 'Statistics Explained article'.
                  SA:178 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SA:178 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SA:178 dct:modified 



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SA:223 estat:StatisticalArticle SA:223.
                  SA:223 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistical-article'.
                  SA:223 dct:title 'Digital economy and society statistics - households and individuals'.  
                  SA:223 dct:description 'Statistics Explained article'.
                  SA:223 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SA:223 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
      

...



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SA:8789 estat:StatisticalArticle SA:8789.
                  SA:8789 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistical-article'.
                  SA:8789 dct:title 'Enlargement countries - finance statistics'.  
                  SA:8789 dct:description 'Statistics Explained article'.
                  SA:8789 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SA:8789 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SA:878



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SA:8987 estat:StatisticalArticle SA:8987.
                  SA:8987 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistical-article'.
                  SA:8987 dct:title 'Disability statistics - financial situation'.  
                  SA:8987 dct:description 'Statistics Explained article'.
                  SA:8987 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SA:8987 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SA:89



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SA:9160 estat:StatisticalArticle SA:9160.
                  SA:9160 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistical-article'.
                  SA:9160 dct:title 'Being young in Europe today - health'.  
                  SA:9160 dct:description 'Statistics Explained article'.
                  SA:9160 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SA:9160 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SA:9160 dct:



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SA:9316 estat:StatisticalArticle SA:9316.
                  SA:9316 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistical-article'.
                  SA:9316 dct:title 'Agri-environmental indicator - soil erosion'.  
                  SA:9316 dct:description 'Statistics Explained article'.
                  SA:9316 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SA:9316 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SA:93



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SA:9467 estat:StatisticalArticle SA:9467.
                  SA:9467 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistical-article'.
                  SA:9467 dct:title 'Maritime accident fatalities in the EU'.  
                  SA:9467 dct:description 'Statistics Explained article'.
                  SA:9467 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SA:9467 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SA:9467 dc

###  3.2 - Insertion of Statistical Explained core data 

Core data --> Excel part of SArticles 

In [34]:
def insert_dat_article_core_data(DB, link_info_table, article_paragraph_table, article_table, mod_resource_info_table, mod_resource_type_table, method): 
  
    for i, row in DB.iterrows():

        id_ = row['link_id']
        
        article_id_ = row["article_id"]
        #Get last update from article table : 
        last_update_ = str( article_table[article_table['id'] == article_id_].last_update.item())
        #Get info from the eurostat_links
        url_ = link_info_table[link_info_table['id'] == id_].url.item()
        title_ = link_info_table[link_info_table['id'] == article_id_].title.item()
        title_ = title_.replace("'","").strip()
        resourcetype_id_ = link_info_table.loc[link_info_table['id'] == id_]['resource_type_id'].item()
        resourceinfo_id_ = link_info_table.loc[link_info_table['id'] == id_]['resource_information_id'].item() 
        #get the label from resourcetype and info  id
        resourceinfo_ = mod_resource_info_table.loc[mod_resource_info_table['id'] == resourceinfo_id_]['uri'].item() 
        resourcetype_ = mod_resource_type_table.loc[mod_resource_type_table['id'] == resourcetype_id_]['uri'].item() 
        
        

        # Construct the query 
        query = """

            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:""" + str(id_) + """ estat:StatisticalDataReport SDR:""" + str(id_) + """.
              SDR:""" + str(id_) + """ dct:type '""" + str(resourcetype_) + """'.
              SDR:""" + str(id_) + """ dct:title '""" + str(title_) + """'.  
              SDR:""" + str(id_) + """ dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:""" + str(id_) + """ estat:resourceInformation '""" + str(resourceinfo_) + """'.
              SDR:""" + str(id_) + """ dct:modified '""" + str(last_update_) + """'.
              SDR:""" + str(id_) + """ dct:source '""" + str(url_) + """'.  
              SDR:""" + str(id_) + """ estat:dataInformation SA:""" + str(article_id_) + """.  

        } }
        ;
            """
        print(query)
        sparql.setQuery(query)
        sparql.method = method
        sparql.setReturnFormat(JSON)
        results = sparql.query().response.read()

In [35]:
insert_dat_article_core_data(DB = ESTAT_V1_dat_article_core_data,
                              link_info_table = ESTAT_V1_dat_link_info,
                             article_paragraph_table= ESTAT_V1_dat_article_paragraph,
                             article_table = ESTAT_V1_dat_article,
                              mod_resource_info_table = ESTAT_V1_mod_resource_information,
                              mod_resource_type_table = ESTAT_V1_mod_resource_type,
                              method = "POST")



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:2907 estat:StatisticalDataReport SDR:2907.
              SDR:2907 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistic-reference-metadata'.
              SDR:2907 dct:title 'Absences from work - quarterly statistics'.  
              SDR:2907 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:2907 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:2907 dct:modified '2021-06-28 09:09:00'.
              SDR:2907 dct:source 'https://ec.eur



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:3082 estat:StatisticalDataReport SDR:3082.
              SDR:3082 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistic-reference-metadata'.
              SDR:3082 dct:title 'Ageing Europe - statistics on social life and opinions'.  
              SDR:3082 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:3082 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:3082 dct:modified '2020-09-28 08:48:00'.
              SDR:3082 dct:source 'h



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:3298 estat:StatisticalDataReport SDR:3298.
              SDR:3298 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistic-reference-metadata'.
              SDR:3298 dct:title 'Agri-environmental indicator - specialisation'.  
              SDR:3298 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:3298 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:3298 dct:modified '2020-04-03 11:15:00'.
              SDR:3298 dct:source 'https://ec



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:3456 estat:StatisticalDataReport SDR:3456.
              SDR:3456 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistic-reference-metadata'.
              SDR:3456 dct:title 'Asia-Europe Meeting (ASEM) - a statistical portrait - tourism'.  
              SDR:3456 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:3456 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:3456 dct:modified '2020-09-10 09:13:00'.
              SDR:3456 dct:so



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:3602 estat:StatisticalDataReport SDR:3602.
              SDR:3602 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistic-reference-metadata'.
              SDR:3602 dct:title 'Chemicals production and consumption statistics'.  
              SDR:3602 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:3602 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:3602 dct:modified '2021-06-25 18:34:00'.
              SDR:3602 dct:source 'https://

...



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:9254 estat:StatisticalDataReport SDR:9254.
              SDR:9254 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistic-reference-metadata'.
              SDR:9254 dct:title 'Air safety statistics in the EU'.  
              SDR:9254 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:9254 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:9254 dct:modified '2021-07-07 10:39:00'.
              SDR:9254 dct:source 'https://ec.europa.eu/eur



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:9317 estat:StatisticalDataReport SDR:9317.
              SDR:9317 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistic-reference-metadata'.
              SDR:9317 dct:title 'Agri-environmental indicator - soil erosion'.  
              SDR:9317 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:9317 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:9317 dct:modified '2020-03-10 17:00:00'.
              SDR:9317 dct:source 'https://ec.e



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:9381 estat:StatisticalDataReport SDR:9381.
              SDR:9381 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistic-reference-metadata'.
              SDR:9381 dct:title 'Ageing Europe ? statistics on housing and living conditions'.  
              SDR:9381 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:9381 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:9381 dct:modified '2020-11-04 16:55:00'.
              SDR:9381 dct:sour



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:9437 estat:StatisticalDataReport SDR:9437.
              SDR:9437 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistic-reference-metadata'.
              SDR:9437 dct:title 'The EU in the world - labour market'.  
              SDR:9437 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:9437 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:9437 dct:modified '2020-05-29 14:02:00'.
              SDR:9437 dct:source 'https://ec.europa.eu



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:9478 estat:StatisticalDataReport SDR:9478.
              SDR:9478 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistic-reference-metadata'.
              SDR:9478 dct:title 'EU international trade in goods - latest developments'.  
              SDR:9478 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:9478 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:9478 dct:modified '2021-07-02 16:55:00'.
              SDR:9478 dct:source 'ht

###  3.3 - Insertion of Statistical Explained articles related elements 

In [36]:
def insert_articles_elements_relations(DB, link_info_table, SEG_table, BGA_table, SA_table, SED_table, method):      
    
    for i, row in DB.iterrows():
        article_id = row["article_id"]
        link_id_ = row["link_id"] #concept et link sont de la meme sequence unique. 
        #Get the resource type from the eurostat_links
        resourcetype_id_ = link_info_table.loc[link_info_table['id'] == link_id_]['resource_type_id'].item()
        relation_ = ""
        #print(resourcetype_id_)
        if (resourcetype_id_ in [2]): relation_ = "estat:relatedLegallnformation"
        if (resourcetype_id_ in [1,6,7,8,9,10]): relation_ = "estat:relatedEditorialContent"
        if (resourcetype_id_ in [11,12,13,14]): relation_ = "estat:relatedStatisticData"
        if (relation_ != "") :
            #Get the prefix   
            o_prefix = ""
            if (link_id_ in SEG_table.id.values): o_prefix = " SEG:"
            if (link_id_ in BGA_table.id.values): o_prefix = " BGA:"
            if (link_id_ in SA_table.id.values): o_prefix = " SA:"
            if (link_id_ in SED_table.article_id.values): o_prefix = " SED:"
            if (o_prefix != "") :
                
                # Construct the query 
                query = """
                    PREFIX SEG: <https://nlp4statref/knowledge/resource/statistics-explained-glossary#>
                    PREFIX BGA: <https://nlp4statref/knowledge/resource/background-article#>
                    PREFIX SA: <https://nlp4statref/knowledge/resource/statistical-article#>
                    PREFIX SED: <https://nlp4statref/knowledge/resource/statistics-explained-data#>

                    PREFIX estat: <https://nlp4statref/knowledge/ontology/> 
                    PREFIX skos: <http://www.w3.org/2004/02/skos/core#>

                    INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                       SA:""" + str(article_id) + ' ' + relation_ + o_prefix  + str(link_id_) + """. 
                    } }
                    ;
                """
                print(query)
                sparql.setQuery(query)
                sparql.method = method
                sparql.setReturnFormat(JSON)
                results = sparql.query().response.read()

In [37]:
insert_articles_elements_relations(DB = ESTAT_V1_dat_article_shared_link,
                                   link_info_table = ESTAT_V1_dat_link_info,
                                   SEG_table = ESTAT_V1_dat_glossary,  
                                   BGA_table=ESTAT_V1_dat_background_article,
                                   SA_table=ESTAT_V1_dat_article, 
                                   SED_table=ESTAT_V1_dat_article_core_data,
                                   method = 'POST')

###  4 - Insertion of Background Articles elements into the KDB. 

###  4.1 - Insertion of Background Articles

In [38]:

## Find the homepage : 
SBA_homepage_id = ESTAT_V1_dat_background_article.loc[ESTAT_V1_dat_background_article['homepage']==1]['id'].item()

In [39]:
def insert_dat_background_article(DB, article_shared_link_table, link_info_table, mod_resource_info_table, mod_resource_type_table, homepage_id, method): 

    for i, row in DB.iterrows():

        id_ = row['id']
        if id_ != homepage_id :    
            last_update_ = str(row["last_update"])

            # Get info from the eurostat_links
            title_ = link_info_table[link_info_table['id'] == id_].title.item()
            title_ = title_.replace("'","").strip()
            url_ = link_info_table[link_info_table['id'] == id_].url.item()
            resourcetype_id_ = link_info_table.loc[link_info_table['id'] == id_]['resource_type_id'].item()
            resourceinfo_id_ = link_info_table.loc[link_info_table['id'] == id_]['resource_information_id'].item() 
            #get the label from resourcetype and info  id
            resourceinfo_ = mod_resource_info_table.loc[mod_resource_info_table['id'] == resourceinfo_id_]['uri'].item() 
            resourcetype_ = mod_resource_type_table.loc[mod_resource_type_table['id'] == resourcetype_id_]['uri'].item() 
            # add source data 
            shared_links = article_shared_link_table[article_shared_link_table['article_id'] == id_]
            if (1 in shared_links['article_division_id'].values) : 
                shared_links_source = shared_links.loc[shared_links['article_division_id']==1]['link_id'].values
                source_query_part = []
                for val in shared_links_source: # if multiple values 
                    subpart = """SBA:""" + str(id_) + """ estat:sourceData SDR:"""   + str(val) + """."""
                    source_query_part.append(subpart)
                source_query_part = '\n'.join(source_query_part)      
            else : source_query_part = ""
            # Construct the query 
            query = """

                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SBA:""" + str(id_) + """ estat:BackgroundArticle SBA:""" + str(id_) + """.
                  SBA:""" + str(id_) + """ dct:type '""" + str(resourcetype_) + """'.
                  SBA:""" + str(id_) + """ dct:title '""" + str(title_) + """'.  
                  SBA:""" + str(id_) + """ dct:description 'Background article'.
                  SBA:""" + str(id_) + """ dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SBA:""" + str(id_) + """ estat:resourceInformation '""" + str(resourceinfo_) + """'.
                  SBA:""" + str(id_) + """ dct:modified '""" + str(last_update_) + """'.
                  SBA:""" + str(id_) + """ dct:source '""" + str(url_) + """'.  
                  """ + source_query_part + """

            } }
            ;
                """
            print(query)
            sparql.setQuery(query)
            sparql.method = method
            sparql.setReturnFormat(JSON)
            results = sparql.query().response.read()

In [40]:
#a mettre à jour 
insert_dat_background_article(DB = ESTAT_V1_dat_background_article,
                   article_shared_link_table = ESTAT_V1_dat_article_shared_link,
                              link_info_table = ESTAT_V1_dat_link_info,
                              mod_resource_info_table = ESTAT_V1_mod_resource_information,
                              mod_resource_type_table = ESTAT_V1_mod_resource_type,
                              homepage_id =  SBA_homepage_id,
                              method = "POST")



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SBA:25 estat:BackgroundArticle SBA:25.
                  SBA:25 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#background-article'.
                  SBA:25 dct:title 'Short-term business statistics introduced'.  
                  SBA:25 dct:description 'Background article'.
                  SBA:25 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SBA:25 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SBA:25 dct:modified '2020-



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SBA:367 estat:BackgroundArticle SBA:367.
                  SBA:367 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#background-article'.
                  SBA:367 dct:title 'Geographical information system of the Commission (GISCO)'.  
                  SBA:367 dct:description 'Background article'.
                  SBA:367 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SBA:367 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SBA



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SBA:1098 estat:BackgroundArticle SBA:1098.
                  SBA:1098 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#background-article'.
                  SBA:1098 dct:title 'Social protection statistics - background'.  
                  SBA:1098 dct:description 'Background article'.
                  SBA:1098 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SBA:1098 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SBA:1098 dct



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SBA:1500 estat:BackgroundArticle SBA:1500.
                  SBA:1500 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#background-article'.
                  SBA:1500 dct:title 'Chapter 6'.  
                  SBA:1500 dct:description 'Background article'.
                  SBA:1500 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SBA:1500 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SBA:1500 dct:modified '2019-01-21 16:03:00'.



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SBA:1854 estat:BackgroundArticle SBA:1854.
                  SBA:1854 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#background-article'.
                  SBA:1854 dct:title 'European system of national and regional accounts - ESA 2010'.  
                  SBA:1854 dct:description 'Background article'.
                  SBA:1854 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SBA:1854 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
           

...



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SBA:10277 estat:BackgroundArticle SBA:10277.
                  SBA:10277 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#background-article'.
                  SBA:10277 dct:title 'Farm structure survey - administrative sources'.  
                  SBA:10277 dct:description 'Background article'.
                  SBA:10277 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SBA:10277 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SBA:10355 estat:BackgroundArticle SBA:10355.
                  SBA:10355 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#background-article'.
                  SBA:10355 dct:title 'EU statistics on income and living conditions (EU-SILC) methodology - housing conditions'.  
                  SBA:10355 dct:description 'Background article'.
                  SBA:10355 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SBA:10355 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SBA:10365 estat:BackgroundArticle SBA:10365.
                  SBA:10365 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#background-article'.
                  SBA:10365 dct:title 'EU statistics on income and living conditions (EU-SILC) methodology - 2012 housing conditions'.  
                  SBA:10365 dct:description 'Background article'.
                  SBA:10365 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SBA:10365 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/res



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SBA:10382 estat:BackgroundArticle SBA:10382.
                  SBA:10382 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#background-article'.
                  SBA:10382 dct:title 'Energy balance - new methodology'.  
                  SBA:10382 dct:description 'Background article'.
                  SBA:10382 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SBA:10382 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
                  SBA:10382 dct:



                PREFIX dct: <http://purl.org/dc/terms/>
                PREFIX estat: <https://nlp4statref/knowledge/ontology/>
                PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
                PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
                INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

                  SBA:10432 estat:BackgroundArticle SBA:10432.
                  SBA:10432 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#background-article'.
                  SBA:10432 dct:title 'Building the System of National Accounts - strategy'.  
                  SBA:10432 dct:description 'Background article'.
                  SBA:10432 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
                  SBA:10432 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
             

###  4.2 - Insertion of Background Articles core data 

Core data --> Excel part of SBArticles 

In [41]:
#a mettre à jour 
def insert_dat_background_article_core_data(DB, link_info_table, article_paragraph_table, article_table, mod_resource_info_table, mod_resource_type_table, method): 
  
    for i, row in DB.iterrows():

        id_ = row['link_id']
        
        article_id_ = row["article_id"]
        #Get last update from article table : 
        last_update_ = str( article_table[article_table['id'] == article_id_].last_update.item())
        #Get info from the eurostat_links
        url_ = link_info_table[link_info_table['id'] == id_].url.item()
        title_ = link_info_table[link_info_table['id'] == article_id_].title.item()
        title_ = title_.replace("'","").strip()
        resourcetype_id_ = link_info_table.loc[link_info_table['id'] == id_]['resource_type_id'].item()
        resourceinfo_id_ = link_info_table.loc[link_info_table['id'] == id_]['resource_information_id'].item() 
        #get the label from resourcetype and info  id
        resourceinfo_ = mod_resource_info_table.loc[mod_resource_info_table['id'] == resourceinfo_id_]['uri'].item() 
        resourcetype_ = mod_resource_type_table.loc[mod_resource_type_table['id'] == resourcetype_id_]['uri'].item() 
        
        

        # Construct the query 
        query = """

            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:""" + str(id_) + """ estat:StatisticalDataReport SDR:""" + str(id_) + """.
              SDR:""" + str(id_) + """ dct:type '""" + str(resourcetype_) + """'.
              SDR:""" + str(id_) + """ dct:title '""" + str(title_) + """'.  
              SDR:""" + str(id_) + """ dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:""" + str(id_) + """ estat:resourceInformation '""" + str(resourceinfo_) + """'.
              SDR:""" + str(id_) + """ dct:modified '""" + str(last_update_) + """'.
              SDR:""" + str(id_) + """ dct:source '""" + str(url_) + """'.  
              SDR:""" + str(id_) + """ estat:dataInformation SBA:""" + str(article_id_) + """.  

        } }
        ;
            """
        print(query)
        sparql.setQuery(query)
        sparql.method = method
        sparql.setReturnFormat(JSON)
        results = sparql.query().response.read()

In [ ]:
#a mettre à jour 
insert_dat_background_article_core_data(DB = ESTAT_V1_dat_background_article_core_data,
                              link_info_table = ESTAT_V1_dat_link_info,
                             article_paragraph_table= ESTAT_V1_dat_article_paragraph,
                             article_table = ESTAT_V1_dat_background_article,
                              mod_resource_info_table = ESTAT_V1_mod_resource_information,
                              mod_resource_type_table = ESTAT_V1_mod_resource_type,
                              method = "POST")



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:4382 estat:StatisticalDataReport SDR:4382.
              SDR:4382 dct:type 'Other'.
              SDR:4382 dct:title 'Migrant integration statistics introduced'.  
              SDR:4382 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:4382 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:4382 dct:modified '2021-02-26 14:02:00'.
              SDR:4382 dct:source 'http://ec.europa.eu/eurostat/web/migrant-integration/statistics-illustrated'.  
              SDR:43



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:6430 estat:StatisticalDataReport SDR:6430.
              SDR:6430 dct:type 'Other'.
              SDR:6430 dct:title 'City statistics â culture and recreation'.  
              SDR:6430 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:6430 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:6430 dct:modified '2020-12-03 13:09:00'.
              SDR:6430 dct:source 'https://ec.europa.eu/eurostat/cache/RCI/#?vis=city.statistics&lang=en'.  
              SDR:6430 es



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:6432 estat:StatisticalDataReport SDR:6432.
              SDR:6432 dct:type 'Other'.
              SDR:6432 dct:title 'City statistics â culture and recreation'.  
              SDR:6432 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:6432 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:6432 dct:modified '2020-12-03 13:09:00'.
              SDR:6432 dct:source 'https://ec.europa.eu/eurostat/cache/BubbleCapital/index.html?lg=en'.  
              SDR:6432 estat



            PREFIX dct: <http://purl.org/dc/terms/>
            PREFIX estat: <https://nlp4statref/knowledge/ontology/>
            PREFIX SDR: <https://nlp4statref/knowledge/resource/statistical-data-report#>
            PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
            
            INSERT { GRAPH <https://nlp4statref/knowledge/ontology/> { 

              SDR:9620 estat:StatisticalDataReport SDR:9620.
              SDR:9620 dct:type 'https://nlp4statref/knowledge/resource/authority/resource-type#statistic-reference-metadata'.
              SDR:9620 dct:title 'Business Cycle Clock'.  
              SDR:9620 dct:publisher 'http://publications.europa.eu/resource/authority/corporate-body/ESTAT'.
              SDR:9620 estat:resourceInformation 'https://nlp4statref/knowledge/resource/authority/resource-information#eurostat'.
              SDR:9620 dct:modified '2021-06-02 11:41:00'.
              SDR:9620 dct:source 'https://ec.europa.eu/eurostat/stati

### See added statements 

In [ ]:
SelectStatements = """

PREFIX SBA: <https://nlp4statref/knowledge/resource/background-article#>
SELECT * FROM <https://nlp4statref/knowledge/ontology/>
WHERE { SBA:25 ?s ?o

}       
"""
sparql.setQuery(SelectStatements)
sparql.method = "POST"
sparql.setReturnFormat(JSON)
results = sparql.query().convert()['results']['bindings']
results = pd.json_normalize(results)
print(results)

In [ ]:
results = sparql.query().convert()['results']['bindings']
results = pd.json_normalize(results)
results